In [ ]:
import time
import concurrent
from concurrent import futures
from typing import Any, List, Dict, Tuple

from PIL import Image
from openai import AzureOpenAI
from tqdm.auto import tqdm

import json
from pathlib import Path

import pandas as pd
import requests
from dotenv import dotenv_values
from smolagents import tool, DuckDuckGoSearchTool
import wikipediaapi


In [ ]:
questions = ['How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.',
       '.rewsna eht sa "tfel" drow eht fo etisoppo eht etirw ,ecnetnes siht dnatsrednu uoy fI',
       'Who nominated the only Featured Article on English Wikipedia about a dinosaur that was promoted in November 2016?',
       'Given this table defining * on the set S = {a, b, c, d, e}\n\n|*|a|b|c|d|e|\n|---|---|---|---|---|---|\n|a|a|b|c|b|d|\n|b|b|c|a|e|c|\n|c|c|a|b|b|a|\n|d|b|e|b|e|d|\n|e|d|b|a|d|c|\n\nprovide the subset of S involved in any possible counter-examples that prove * is not commutative. Provide your answer as a comma separated list of the elements in the set in alphabetical order.',
       'Examine the video at https://www.youtube.com/watch?v=1htKBjuUWec.\n\nWhat does Teal\'c say in response to the question "Isn\'t that hot?"',
       "What is the surname of the equine veterinarian mentioned in 1.E Exercises from the chemistry materials licensed by Marisa Alviar-Agnew & Henry Agnew under the CK-12 license in LibreText's Introductory Chemistry materials as compiled 08/21/2023?",
       "I'm making a grocery list for my mom, but she's a professor of botany and she's a real stickler when it comes to categorizing things. I need to add different foods to different categories on the grocery list, but if I make a mistake, she won't buy anything inserted in the wrong category. Here's the list I have so far:\n\nmilk, eggs, flour, whole bean coffee, Oreos, sweet potatoes, fresh basil, plums, green beans, rice, corn, bell pepper, whole allspice, acorns, broccoli, celery, zucchini, lettuce, peanuts\n\nI need to make headings for the fruits and vegetables. Could you please create a list of just the vegetables from my list? If you could do that, then I can figure out how to categorize the rest of the list into the appropriate categories. But remember that my mom is a real stickler, so make sure that no botanical fruits end up on the vegetable list, or she won't get them when she's at the store. Please alphabetize the list of vegetables, and place each item in a comma separated list.",
       'Who did the actor who played Ray in the Polish-language version of Everybody Loves Raymond play in Magda M.? Give only the first name.',
       'How many at bats did the Yankee with the most walks in the 1977 regular season have that same season?',
       'On June 6, 2023, an article by Carolyn Collins Petersen was published in Universe Today. This article mentions a team that produced a paper about their observations, linked at the bottom of the article. Find this paper. Under what NASA award number was the work performed by R. G. Arendt supported by?',
       "Where were the Vietnamese specimens described by Kuznetzov in Nedoshivina's 2010 paper eventually deposited? Just give me the city name without abbreviations.",
       "What country had the least number of athletes at the 1928 Summer Olympics? If there's a tie for a number of athletes, return the first in alphabetical order. Give the IOC country code as your answer.",
       "Who are the pitchers with the number before and after Taishō Tamai's number as of July 2023? Give them to me in the form Pitcher Before, Pitcher After, use their last names only, in Roman characters.",
       'What is the first name of the only Malko Competition recipient from the 20th Century (after 1977) whose nationality on record is a country that no longer exists?']

In [ ]:
from smolagents import GoogleSearchTool
import requests
import urllib.request
from markdownify import markdownify as md
from bs4 import BeautifulSoup
from dotenv import dotenv_values
from openai import AzureOpenAI
import json



def get_search_results_for(query):
    encoded_query = urllib.parse.urlencode({'q': query})
    url = f'https://html.duckduckgo.com/html?q={encoded_query}'

    request = urllib.request.Request(url)
    request.add_header('User-Agent', 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36')

    raw_response = urllib.request.urlopen(request).read()
    html = raw_response.decode("utf-8")

    soup = BeautifulSoup(html, 'html.parser')
    a_results = soup.select("a.result__a")

    links = []
    for a_result in a_results:
        # print(a_result)
        url = a_result.attrs['href']
        title = a_result.text
        links.append({"title": title,  "url": url} )

    return links

search_tool = GoogleSearchTool("serper")

def get_google_search_results_for(query: str):
    return search_tool.forward(query)


def load_page_content(url) -> str:
    response = requests.get(url, headers={'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
    page_content = response.content.decode('utf-8')
    page_content_md = md(page_content)

    return page_content_md



In [ ]:
tools = [{
        "type": "function",
        "function": {
            "name": "get_search_results_for",
            "description": "Returns the top 10 results for a DuckDuckGo query.",
            "parameters": {
                "type": "object",
                "properties": {
                    "query": {
                        "type": "string",
                        "description": "query to search for on DuckDuckGo"
                    }
                },
                "required": [
                    "query"
                ],
                "additionalProperties": False
            },
            "strict": True
        }
    },
    {
        "type": "function",
        "function": {
            "name": "load_page_content",
            "description": "Returns the content of a particular webpage.",
            "parameters": {
                "type": "object",
                "properties": {
                    "url": {
                        "type": "string",
                        "description": "Url of the webpage for which to retrieve the content"
                    }
                },
                "required": [
                    "url"
                ],
                "additionalProperties": False
            },
            "strict": True
        }
    }
]

def call_function(name, args):
    if name == "get_search_results_for":
        return get_google_search_results_for(**args)
    if name == "load_page_content":
        return load_page_content(**args)

    return None


In [ ]:
query = questions[2]
config = dotenv_values()

client = AzureOpenAI(
    api_key=config["AZURE_OPENAI_API_KEY"],
    azure_endpoint=config["AZURE_OPENAI_API_BASE"],
    api_version=config["AZURE_OPENAI_API_VERSION"]
)
openai_chatmodel = config["AZURE_OPENAI_CHAT_MODEL"]

GRAY = "\033[90m"
BOLD = "\033[1m"
RESET = "\033[0m"


messages = [
    {
        "role": "system",
        "content": "You are a general AI assistant. I will ask you a question. Report your thoughts, and finish your answer with the following template: FINAL ANSWER: [YOUR FINAL ANSWER]. YOUR FINAL ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings. If you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise. If you are asked for a string, don't use articles, neither abbreviations (e.g. for cities), and write the digits in plain text unless specified otherwise. If you are asked for a comma separated list, apply the above rules depending of whether the element to be put in the list is a number or a string."
    },
    {"role": "user", "content": query}
]

total_input_token_count = 0
total_output_token_count = 0

while True:
    completion = client.chat.completions.create(
        model=openai_chatmodel,
        messages=messages,
        tools=tools
    )

    total_input_token_count += completion.usage.prompt_tokens
    total_output_token_count += completion.usage.completion_tokens

    if completion.choices[0].finish_reason == "stop":
        print(f"{BOLD}Final answer: {completion.choices[0].message.content}{RESET}")
        break
    elif completion.choices[0].finish_reason == "tool_calls":
        messages.append(completion.choices[0].message)
        for tool_call in completion.choices[0].message.tool_calls:
            name = tool_call.function.name
            args = json.loads(tool_call.function.arguments)

            result = call_function(name, args)
            print(f"Called {BOLD}{name}({args}){RESET} and it returned {GRAY}{str(result)[:300]}{RESET}")

            messages.append({
                "role": "tool",
                "tool_call_id": tool_call.id,
                "content": str(result)
            })
    else:
        raise Exception("We're not supposed to be here")

In [ ]:
def run_agent(task: str):

    messages = [
        {
            "role": "system",
            "content": "You are a general AI assistant. I will ask you a question. Report your thoughts, and finish your answer with the following template: FINAL ANSWER: [YOUR FINAL ANSWER]. YOUR FINAL ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings. If you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise. If you are asked for a string, don't use articles, neither abbreviations (e.g. for cities), and write the digits in plain text unless specified otherwise. If you are asked for a comma separated list, apply the above rules depending of whether the element to be put in the list is a number or a string."
        },
        {"role": "user", "content": task}
    ]

    while True:
        completion = client.chat.completions.create(
            model=openai_chatmodel,
            messages=messages,
            tools=tools
        )

        if completion.choices[0].finish_reason == "stop":
            print(f"{BOLD}Final answer: {completion.choices[0].message.content}{RESET}")
            return completion.choices[0].message.content
        elif completion.choices[0].finish_reason == "tool_calls":
            messages.append(completion.choices[0].message)
            for tool_call in completion.choices[0].message.tool_calls:
                name = tool_call.function.name
                args = json.loads(tool_call.function.arguments)

                result = call_function(name, args)
                print(f"Called {BOLD}{name}({args}){RESET} and it returned {GRAY}{str(result)[:300]}{RESET}")

                messages.append({
                    "role": "tool",
                    "tool_call_id": tool_call.id,
                    "content": str(result)
                })
        else:
            raise Exception("We're not supposed to be here")

run_agent(questions[4])